## Utilização do Leaflet a partir do Folium
Apresentação de algumas das funcionalidades do pacote python FOLIUM, que possibilita a geração de mapas por meio da biblioteca Javascript Leaflet (http://leafletjs.com/).

In [57]:
import os
import folium
import sys

In [58]:
lat, long = -23.563887, -46.628290

zoom_start = 8

### Parâmetros para a geração do Mapa (folium.map)
- Localização inicial (Latitude, Logitude);
- Mapa base (Tile Layer);
- Zoom inicial.

O Folium disponibiliza por padrão os seguinte Mapas base (Tile layers):
- “OpenStreetMap”
- “Mapbox Bright” 
- “Mapbox Control Room”
- “Stamen” (Terrain, Toner, and Watercolor)
- “Cloudmade” (Must pass API key)
- “Mapbox” (Must pass API key)
- “CartoDB” (positron , dark_matter)

In [59]:
m = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)

m.save(os.path.join('results', 'basemap.html'))

m

## Utilização de uma base de dados geográfica (Gazetteer)
Utilização do pacote geocoder (https://github.com/DenisCarriere/geocoder) para a identificação das coordenadas de um endereço.

In [60]:
import geocoder

In [61]:
 g = geocoder.google('Rua Augusta, 973, São Paulo')

In [62]:
g.json

{'accuracy': 'ROOFTOP',
 'address': 'R. Augusta, 973 - Consolação, São Paulo - SP, 01305-100, Brazil',
 'bbox': {'northeast': [-23.5521084197085, -46.6537709197085],
  'southwest': [-23.5548063802915, -46.6564688802915]},
 'city': 'São Paulo',
 'confidence': 9,
 'country': 'BR',
 'county': 'São Paulo',
 'encoding': 'utf-8',
 'housenumber': '973',
 'lat': -23.5534574,
 'lng': -46.6551199,
 'location': 'Rua Augusta, 973, São Paulo',
 'ok': True,
 'place': 'ChIJ30LcjTRYzpQRWdc0cNlgZHk',
 'postal': '01305-100',
 'provider': 'google',
 'quality': 'street_address',
 'state': 'SP',
 'status': 'OK',
 'status_code': 200,
 'street': 'R. Augusta',
 'sublocality': 'Consolação'}

In [63]:
g.json['lat'], g.json['lng']

(-23.5534574, -46.6551199)

## Inclusão de um marcador (ponto) no mapa

In [64]:
folium.Marker(
    location=[g.json['lat'], g.json['lng']],
    popup='FAM - Faculdade das Americas',
    icon=folium.Icon(color='green', icon='ok-sign')
).add_to(m)

In [65]:
m.save(os.path.join('results', 'basemap_marker.html'))
m

## Inclusão de mapas base adicionais
A partir da inclusão de um componente para controle de Layers, possibilita também que os Mapas Base possam ser alternados pelo usuário.

In [66]:
folium.TileLayer('Stamen Terrain').add_to(m)
folium.TileLayer('Stamen Toner').add_to(m)
folium.LayerControl().add_to(m)

In [67]:
m.save(os.path.join('results', 'basemap_marker_add_base_maps.html'))
m

## Inclusão de marcadores (pontos) provenientes de um arquivo CSV.
Leitura de um arquivo CSV, com ocorrências de espécies de animais em São Paulo, usando o pacote PANDAS, e a plotagem dos dados no mapa. (Fonte dos dados de ocorrências: Portal do ICMBio)

In [68]:
lat, long = -23.563887, -46.628290
zoom_start = 6

m2 = folium.Map(location=[lat, long], tiles="Stamen Terrain", zoom_start=zoom_start)

m2.save(os.path.join('results', 'basemap2.html'))

m2

In [69]:
import pandas as pd
#species occurrences in the State of Sao Paulo
occurrences = pd.read_csv('data/occ/DadosOcorrencias.csv', delimiter=';')
MAX_RECORDS = 1000

for record in occurrences[0:MAX_RECORDS].iterrows():
    folium.Marker(location = [record[1]['Latitude'],record[1]['Longitude']], popup=record[1]['Espécie']).add_to(m2)



In [70]:
m2.save(os.path.join('results', 'basemap2_markers.html'))

m2

## Inclusão de uma camada de cluster
Para melhor visualização, os marcadores (pontos), que representam as ocorrências de espécies são agrupados em clusters, que se atualizam conforme a mudança do zoom de visualização.

In [71]:
lat, long = -23.563887, -46.628290
zoom_start = 7

m3 = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)
marker_cluster = folium.MarkerCluster("occ").add_to(m3)

for record in occurrences[0:MAX_RECORDS].iterrows():
    folium.Marker(location = [record[1]['Latitude'],record[1]['Longitude']]).add_to(marker_cluster)

m3.save(os.path.join('results', 'basemap3_clusters.html'))

m3

## Adicionando camadas de serviços WMS
Criação de camadas de dados a partir do consumo de serviços WMS (Web Map Service) de um servidor externo (Servidor de Mapas do ICMBio).

In [72]:
folium.WmsTileLayer(name='&Aacute;reas Priorit&aacute;rias',
                    layers = 'areas_prioritarias',            
                    url='http://mapas.icmbio.gov.br/cgi-bin/mapserv?map=/geodados/icmbio/mapfile/mma_AreasPrioritarias.map&amp;',
                    format='image/png').add_to(m3)

folium.WmsTileLayer(name='Terras Ind&iacute;genas',
                    layers = 'ti',            
                    url='http://mapas.icmbio.gov.br/cgi-bin/mapserv?map=/geodados/icmbio/mapfile/funai_TerraIndigena.map&amp;',
                    format='image/png').add_to(m3)




folium.LayerControl().add_to(m3)

m3.save(os.path.join('results', 'basemap3_clusters_wms.html'))

m3


## Utilização de plugins do Leaflet por meio do FOLIUM
Utilização do plugin de Mapa de Calor (HeatMap) para a verificação das áreas com maior quantidade de ocorrências de animais.

In [73]:
from folium.plugins import HeatMap
import csv

lat, long = -23.563887, -46.628290
zoom_start = 7
MAX_RECORDS = 1000

records = []
for record in occurrences[0:MAX_RECORDS].iterrows():
    records.append([record[1]['Latitude'],record[1]['Longitude']])
    
m4 = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)

HeatMap(records).add_to(m4)

m4.save(os.path.join('results', 'basemap4_HeatMap.html'))

m4

## Inclusão de uma camada de dados a partir de um arquivo GEOJSON
Inclusão de uma camada de dados no mapa a partir de um arquivos geojson, que representa os biomas brasileiros. (Fonte: ICMBio)

In [74]:
import json

geo_json_data = json.load(open('data/brasil/biomas.geojson'))
lat, long = -23.563887, -46.628290
zoom_start = 7

m5 = folium.Map(location=[lat, long], tiles="OpenStreetMap", zoom_start=zoom_start)

folium.GeoJson(geo_json_data, name='Biomas', overlay=True).add_to(m5)

folium.LayerControl().add_to(m5)

m5.save(os.path.join('results', 'basemap5_GeoJSON.html'))

m5
